In [34]:
import numpy as np
import pandas as pd
from Classes.PercepTeacher import PerceptronTeacher
from Functions.function_of_activation import sigmoid, dsigmoid
from Functions.errorFunctions import MSE
from Classes.Layer import Layer
from Classes.LayerGen import LayerGenerator
from random import random
from Classes.Perceptron import Perceptron
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split
np.random.seed(1)


In [35]:
x = np.array([[1, 2, 3], [2, 3, 4], [4, 5, 6],
             [7, 8, 1], [9, 8, 1], [7, 2, 1], [5, 8, 1], [1, 8, 2], [7, 3, 1], [7, 7, 7], [2, 2, 1], [1, 1, 7], [4, 3, 2], [7, 8, 1]])
y = np.sum(x, axis=1).reshape(x.shape[0], 1).reshape(x.shape[0], 1)
a = 0
b = 1
x_min_max = a + (x - x.min())/(x.max() - x.min()) * (b-a)
y_min_max = a + (y - y.min())/(y.max() - y.min()) * (b-a)


In [36]:
layer_mass = LayerGenerator(sizes_of_input_layer=3,
                            sizes_of_hidden_layers=[6, 4, 2],
                            sizes_of_output_layer=1,
                            summators=[lambda w, x, d: w.dot(x.T) + d, 
                                       lambda w, x, d: w.dot(x.T) + d,
                                       lambda w, x, d: w.dot(x.T) + d,
                                       lambda w, x, d: w.dot(x.T) + d],
                            dsummators=[lambda w, x, d: (x, d),
                                        lambda w, x, d: (x, d),
                                        lambda w, x, d: (x, d),
                                        lambda w, x, d: (x, d)],
                            activation_functions=[sigmoid,
                                                  sigmoid,
                                                  sigmoid,
                                                  sigmoid],
                            dactivation_functions=[dsigmoid,
                                                   dsigmoid,
                                                   dsigmoid,
                                                   dsigmoid],
                            function_of_generation=lambda a, b: np.random.rand(a, b)).generate()
layer_mass


In [37]:
a = Perceptron(layer_mass)
res = [a.predict(i)[0] for i in x_min_max]
print(MSE(res, y_min_max))
for p, y in zip(res, y_min_max):
    print(f'p:{p},\t y:{y},\t d:{abs(p-y)}')


0.1521928670524091
p:[0.71849538],	 y:[0.0625],	 d:[0.65599538]
p:[0.71881752],	 y:[0.25],	 d:[0.46881752]
p:[0.71932998],	 y:[0.625],	 d:[0.09432998]
p:[0.71961496],	 y:[0.6875],	 d:[0.03211496]
p:[0.71973384],	 y:[0.8125],	 d:[0.09276616]
p:[0.71900589],	 y:[0.3125],	 d:[0.40650589]
p:[0.71948163],	 y:[0.5625],	 d:[0.15698163]
p:[0.71921708],	 y:[0.375],	 d:[0.34421708]
p:[0.71912651],	 y:[0.375],	 d:[0.34412651]
p:[0.71973087],	 y:[1.],	 d:[0.28026913]
p:[0.71847081],	 y:[0.],	 d:[0.71847081]
p:[0.71861],	 y:[0.25],	 d:[0.46861]
p:[0.71890163],	 y:[0.25],	 d:[0.46890163]
p:[0.71961496],	 y:[0.6875],	 d:[0.03211496]


In [38]:
def batch_spliter(x, y, size, num):
    batches = list()
    for _ in range(num):
        js = np.random.shuffle(np.arange(size))
        batches.append((x[js][0], y[js][0]))
    return batches


In [39]:
k = []
for i in layer_mass:
    k.append(i.get_weights())
    print(i.get_weights())


[[4.17022005e-01 7.20324493e-01 1.14374817e-04]
 [3.02332573e-01 1.46755891e-01 9.23385948e-02]
 [1.86260211e-01 3.45560727e-01 3.96767474e-01]
 [5.38816734e-01 4.19194514e-01 6.85219500e-01]
 [2.04452250e-01 8.78117436e-01 2.73875932e-02]
 [6.70467510e-01 4.17304802e-01 5.58689828e-01]]
[[0.87638915 0.89460666 0.08504421 0.03905478 0.16983042 0.8781425 ]
 [0.09834683 0.42110763 0.95788953 0.53316528 0.69187711 0.31551563]
 [0.68650093 0.83462567 0.01828828 0.75014431 0.98886109 0.74816565]
 [0.28044399 0.78927933 0.10322601 0.44789353 0.9085955  0.29361415]]
[[0.21162812 0.26554666 0.49157316 0.05336255]
 [0.57411761 0.14672857 0.58930554 0.69975836]]
[[0.69440016 0.41417927]]


In [40]:
teacher = PerceptronTeacher(layers=layer_mass,
                                 step=1,
                                 batch_spliter=lambda a, b: batch_spliter(a, b, a.shape[0]//2, 1),
                                 epochs=100,
                                 error_function=MSE,
                                 derror_function=lambda x, y: 2 * x - 2 * y)


In [41]:
tl = teacher.teach(x_min_max, y_min_max)


4 5 4 4
shapes	a: (1, 2), s: (1, 1)
df:  (1, 1) [[0.2022597678475153]]
d_output:  (1, 1) [[1.3119907649023477]]
a:  (1, 2) [[0.7379081064645104, 0.9045683623804218]]
s:  (1, 1) [[0.9370104280314946]]
W:  (1, 2) [[0.6944001577277451, 0.41417926952690265]]
B:  (1, 1) [[0.04995345894608716]]

res
1)  (1, 1) [[0.26536294752723283]]
2.1)  (1, 2) [[0.7379081064645104, 0.9045683623804218]]
2.2)  (1, 1) [[0.04995345894608716]]
3)  (1, 2) [[0.1958134701356616, 0.2400389268811508]]
db:  (1, 1) [[0.013255797105114306]]
W_Step:  (1, 2) [[0.0979067350678308, 0.1200194634405754]]
shapes	a: (1, 4), s: (2, 1)
df:  (2, 1) [[0.19339973287847118], [0.08632444016082369]]
d_output:  (1, 2) [[0.1958134701356616, 0.2400389268811508]]
a:  (1, 4) [[0.8901595194534325, 0.8967279636750205, 0.9299707733537611, 0.9207792041696352]]
s:  (2, 1) [[1.0351241189100937], [2.2490477275690415]]
W:  (2, 4) [[0.21162811600005904, 0.2655466593722262, 0.4915731592803383, 0.053362545117080384], [0.5741176054920131, 0.146728574

In [42]:
for i in tl:
    print(i.get_weights())


[[0.51292795 0.82989166 0.00296497]
 [0.39823851 0.25632306 0.09518919]
 [0.28216615 0.4551279  0.39961807]
 [0.63472268 0.52876169 0.68807009]
 [0.30035819 0.98768461 0.03023819]
 [0.76637345 0.52687197 0.56154042]]
[[ 0.86854852  0.87088576  0.0521647   0.00737467  0.1574352   0.85443421]
 [ 0.0905062   0.39738672  0.92501002  0.50148517  0.67948189  0.29180734]
 [ 0.6786603   0.81090477 -0.01459123  0.7184642   0.97646587  0.72445736]
 [ 0.27260336  0.76555842  0.0703465   0.41621341  0.89620028  0.26990586]]
[[0.22279168 0.26600841 0.48698154 0.04308246]
 [0.58528117 0.14719033 0.58471392 0.68947828]]
[[ 0.07608679 -0.31117779]]


In [43]:
for i, j in zip(k, tl):
    print(i - j.get_weights())


[[-0.09590594 -0.10956717 -0.00285059]
 [-0.09590594 -0.10956717 -0.00285059]
 [-0.09590594 -0.10956717 -0.00285059]
 [-0.09590594 -0.10956717 -0.00285059]
 [-0.09590594 -0.10956717 -0.00285059]
 [-0.09590594 -0.10956717 -0.00285059]]
[[0.00784063 0.0237209  0.03287951 0.03168012 0.01239522 0.02370829]
 [0.00784063 0.0237209  0.03287951 0.03168012 0.01239522 0.02370829]
 [0.00784063 0.0237209  0.03287951 0.03168012 0.01239522 0.02370829]
 [0.00784063 0.0237209  0.03287951 0.03168012 0.01239522 0.02370829]]
[[-0.01116357 -0.00046176  0.00459162  0.01028008]
 [-0.01116357 -0.00046176  0.00459162  0.01028008]]
[[0.61831337 0.72535706]]


In [44]:
a = Perceptron(tl)
res = [a.predict(i)[0] for i in x_min_max]
print(MSE(res, y_min_max))
for p, y in zip(res, y_min_max):
    print(f'p:{p},\t y:{y},\t d:{abs(p-y)}')


0.07813615255346207
p:[0.44521614],	 y:[0.0625],	 d:[0.38271614]
p:[0.44509208],	 y:[0.25],	 d:[0.19509208]
p:[0.44489861],	 y:[0.625],	 d:[0.18010139]
p:[0.44477047],	 y:[0.6875],	 d:[0.24272953]
p:[0.44472717],	 y:[0.8125],	 d:[0.36777283]
p:[0.44499321],	 y:[0.3125],	 d:[0.13249321]
p:[0.44482001],	 y:[0.5625],	 d:[0.11767999]
p:[0.44492675],	 y:[0.375],	 d:[0.06992675]
p:[0.44494791],	 y:[0.375],	 d:[0.06994791]
p:[0.44474821],	 y:[1.],	 d:[0.55525179]
p:[0.44520905],	 y:[0.],	 d:[0.44520905]
p:[0.44519682],	 y:[0.25],	 d:[0.19519682]
p:[0.44504363],	 y:[0.25],	 d:[0.19504363]
p:[0.44477047],	 y:[0.6875],	 d:[0.24272953]
